# Poro34B Lora fine-tuning with S-Group's data

In [ ]:
# This script finetunes the Poro34B model with 185 Questions and Answers pair

## Initialization

In [2]:
# pip install peft, all other Python libraries are already in AWS image
!pip install peft

In [3]:
import torch
import json
from transformers import AutoModelForCausalLM, AutoTokenizer 
from transformers import TrainingArguments, Trainer
from transformers import pipeline
from peft import  get_peft_model, PromptTuningConfig, TaskType, PromptTuningInit
from datasets import load_dataset

2024-02-29 16:17:22.775245: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [4]:
# this checks wether we have GPU
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

In [4]:
print(device)

cpu


## Foundation model import

In [5]:
# Foundation model
model_name='LumiOpen/Poro-34B'

In [6]:
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [7]:
branch = "1000B"
model = AutoModelForCausalLM.from_pretrained(model_name,
    torch_dtype=torch.bfloat16,
    revision=branch,
)

Loading checkpoint shards:   0%|          | 0/14 [00:00<?, ?it/s]

## Setting up the Lora parameters

In [11]:
from peft import LoraConfig, get_peft_model

In [12]:
config = LoraConfig(
    r=8,
    lora_alpha=8,
    target_modules=["query_key_value"],
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM"
)

In [13]:
peft_model = get_peft_model(model, config)

In [14]:
trainable_params = 0
all_param = 0

# iterating over all parameters
for _, param in peft_model.named_parameters():
    # adding parameters to total
    all_param += param.numel()
    # adding parameters to trainable if they require a graident
    if param.requires_grad:
        trainable_params += param.numel()

# print number of trainable parameters
print(f"trainable params: {trainable_params}")
print(f"all params: {all_param}")
print(f"trainable: {100 * trainable_params / all_param:.2f}%")

trainable params: 12386304
all params: 34229336064
trainable: 0.04%


## Preparing the training data

In [15]:
# prepare the data for training
def prepare_train_data(data):
    text_input = data['text']
    tokenized_input = tokenizer(text_input, return_tensors='pt', padding=True)
    tokenized_input['labels'] = tokenized_input['input_ids']
    return tokenized_input

In [16]:
dataset = load_dataset("json", data_files="prompts_185.json")

Generating train split: 0 examples [00:00, ? examples/s]

In [17]:
train_dataset = dataset['train'].map(prepare_train_data, batched=True, remove_columns=["text"])

Map:   0%|          | 0/185 [00:00<?, ? examples/s]

## Setting up the training parameters

In [18]:
from transformers import DataCollatorForLanguageModeling

In [19]:
trainer = Trainer(
    model=peft_model,
    train_dataset=train_dataset,
    args=TrainingArguments(
        per_device_train_batch_size=4,
        gradient_accumulation_steps=4,
        warmup_steps=20,
        max_steps=20,
        learning_rate=1e-3,
        logging_steps=1,
        output_dir='outputs',
    ),
    data_collator=DataCollatorForLanguageModeling(tokenizer, mlm=False)
)

In [ ]:
trainer.train()

/opt/conda/lib/python3.10/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
wandb: Currently logged in as: timo-au-laine. Use `wandb login --relogin` to force relogin


You're using a BloomTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


## Saving the finetuned model

In [ ]:
model_id185 = "Poro-34B-Lora-185"

In [ ]:
peft_model.save_pretrained(model_id185)

In [ ]:
!ls -lh {model_id185}  # Lora parameters file size

## Testing

In [8]:
def generate_output(model, inputs, max_new_tokens=100):
    outputs = model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=max_new_tokens,
        temperature=0.1,
    )
    return outputs

### Original model

In [9]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Mikä on osuusmaksu ja miksi se pitää maksaa? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Mikä on osuusmaksu ja miksi se pitää maksaa? }```, what is the answer? Answer: Osuusmaksu on osuuskaupan osuusmaksu, joka maksetaan liittymisen yhteydessä. Osuusmaksu on sijoitus osuuskauppaan ja se palautetaan, kun jäsen eroaa osuuskaupasta. Osuusmaksun suuruus vaihtelee osuuskaupoittain. Osuusmaksun suuruus on 100 euroa. Osuusmaksu on sijoitus osuuskauppaan ja se palautetaan, kun jäsen eroaa osuuskaupasta. Osuusmaksun suuruus vaihtelee osuuskaupoittain. Osuusmaksun suuruus on 100 euroa. Osuusmaksu on sijoitus osuuskauppaan ja se palautetaan, kun jäsen eroaa osuuskaupasta. Osuusmaksun suuruus vaihtelee osuuskaupoittain.']


In [10]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Mistä näen S-Tilini tapahtumat ja saldon? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Mistä näen S-Tilini tapahtumat ja saldon? }```, what is the answer? Answer: S-Pankin verkkopankissa. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the first sentence in the paragraph. The answer is the']


### Finetuned model

In [27]:
from peft import PeftModel

In [28]:
loaded_model = PeftModel.from_pretrained(model,model_id185,is_trainable=False)

In [29]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Mikä on osuusmaksu ja miksi se pitää maksaa? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(loaded_model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Mikä on osuusmaksu ja miksi se pitää maksaa? }```, what is the answer? Answer: {Osuusmaksun suuruus on 100 euroa. Se maksetaan vain kerran, ja se palautetaan osuuskaupan asiakasomistajuudesta luovuttaessa. Osuusmaksun voi maksaa kerralla kokonaan tai kerryttää sitä Bonuksilla. Osuusmaksun voi maksaa myös S-Etukortilla, jolloin se veloitetaan S-Etukorttiin liitetyltä maksuvälineeltä.}\n\n{Osuusmaksun voi maksaa myös S-ryhmän lahjakortilla. Lahjakortin saldo ei kuitenkaan kerrytä Bonusta.}\n\n{Osuusmaksun voi maksaa myös S-ryhmän lahjak']


In [30]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Mistä näen S-Tilini tapahtumat ja saldon? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(loaded_model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Mistä näen S-Tilini tapahtumat ja saldon? }```, what is the answer? Answer: {S-Tilin tapahtumat ja saldo ovat nähtävissä S-mobiilissa ja S-Pankin verkkopankissa.}\n\n{S-mobiilissa S-Tilin tapahtumat ja saldo ovat nähtävissä S-Etukortti-osiossa.}\n\n{S-Pankin verkkopankissa S-Tilin tapahtumat ja saldo ovat nähtävissä Tilit-osiossa.}\n\n{S-Tilin tapahtumat ja saldo ovat nähtävissä myös S-mobiilin ja S-Pankin verkkopankin S-Etukortti- ja Tilit-osiossa, kun olet']
